# Set up

1. Use Python 3.11.9
2. make venv
3. pip install -r requirements.txt

just read the README

## Imports

In [56]:
import pandas as pd
import numpy as np
import folium
import requests
from dotenv import load_dotenv
import os
import geopandas as gpd
import branca.colormap as cm
from branca.element import MacroElement, Template

df = pd.read_excel('data/practice clean data.xlsx')
multiplier_df = pd.read_excel('data/multiplier.xlsx')
multiplier_df.set_index(['Country'], inplace=True)

df.dropna(subset=['Latitude', 'Longitude','Province'], inplace=True)
# df = df[df['Status'] == 'Active'] # Indonesia decided to not have a status for status
df['Address'] = df['Address'].astype(str).str.replace("\\", "\\\\") # Escape backslashes, thanks India

load_dotenv()
google_maps_api_key = os.getenv('GOOGLE_MAPS_API_KEY')

## Constants and Dicts

In [57]:
linear = cm.LinearColormap(['green', 'yellow', 'red'], vmin=0, vmax=100)
geoboundaries_base_url = 'https://www.geoboundaries.org/api/current/gbOpen/'

store_type = {
    'Eye Rafiki - Full refraction entrepreneur': 'FRE (MMO, EMO, EM, ER)',
    'Eye Mitro - Full refraction entrepreneur': 'FRE (MMO, EMO, EM, ER)',
    'Digital Eye Mitra - Full refraction entrepreneur': 'FRE (MMO, EMO, EM, ER)',
    'Eye Mitra - Full refraction entrepreneur': 'FRE (MMO, EMO, EM, ER)',
    'Mitra Mata Optician - Full refraction entrepreneur': 'FRE (MMO, EMO, EM, ER)',
    'Mitra Mata - Full refraction entrepreneur': 'FRE (MM)',
    'Vision Centre - Vision Centre': 'VC',
    'Value Added Hospitals - Value Added Hospitals': 'VAH',
    'Eye Partner - Eye Partner': 'EP',
    'RAP - Readers Access Point': 'RAP',
    'Hospital - Hospital': 'Hospital (not VAH)',
    'Wholesaler - Wholesaler': 'Wholesaler',
    'Retail - Retail': 'Retail',
    'Mobile Unit - Mobile Unit': 'Mobile Unit',
    'Wholesaler/Distributor - Wholesaler/Distributor': 'Wholesaler/Distributor'

}

country_codes = {
    'Cambodia': 'KHM',
    'China': 'CHN',
    'India': 'IND',
    'Indonesia': 'IDN',
    'Bangladesh': 'BGD',
    'Mexico': 'MEX',
    'Brazil': 'BRA',
    'Kenya': 'KEN',
    'Liberia': 'LBR',
    'Rwanda': 'RWA',
    'South Africa': 'ZAF',
    'Gambia': 'GMB',
    'Zambia': 'ZMB',
    'Malawi': 'MWI',
    'Ghana': 'GHA',
    'Eswatini': 'SWZ',
}

def get_store_type_color(store_type):
    store_colors = {
        "FRE (MMO, EMO, EM, ER)": "blue",
        "FRE (MM)": "brown", 
        "VC": "green",
        "VAH": "red",
        "EP": "yellow",
        "RAP": "purple",
        "Hospital (not VAH)": "orange",
        "Wholesaler": "pink",
        "Retail": "lime",
        "Mobile Unit": "cyan",
        "Wholesaler/Distributor": "gray"
    }
    return store_colors.get(store_type, 'black')

# colour choices:
# "red", "blue", "green", "yellow", "purple", "orange", "pink", "brown", 
# "black", "white", "gray", "grey", "cyan", "magenta", "lime", "olive", 
# "navy", "teal", "maroon", "aqua", "silver", "gold"

## Funcs

In [58]:
def make_points(df, store_type, curr_map):
    point_layer = folium.FeatureGroup(name=str(store_type)).add_to(curr_map)

    store_df = df[df['Store Type'] == store_type]

    if pd.isna(store_type):
        store_df = df[df['Store Type'].isna()]

    for idx, row in store_df.iterrows():
        folium.Circle(
            location=[row['Latitude'], row['Longitude']],  # Center of the circle
            radius=5000,  # 5 km in meters
            color=get_store_type_color(store_type),  # Circle border color
            fill=True,  # Fill the circle
            fill_color=get_store_type_color(store_type),  # Circle fill color
            fill_opacity=0.1,  # Transparency of the fill
            tooltip=folium.Tooltip(
        f"<b>Company:</b> {row['Company']}<br>"
        f"<b>Address:</b> {row['Address']}<br>"
        f"<b>Store Type:</b> {store_type}",
        sticky=True
            ),
            parse_html=True
        ).add_to(point_layer)

def get_geojsons(country_codes):
    gdf = gpd.GeoDataFrame()
    gdf_list = []

    for code in country_codes:
        url = f"{geoboundaries_base_url}{code}/ADM1/"
        response = requests.get(url)
        data = response.json()
        
        if 'simplifiedGeometryGeoJSON' in data:
            geojson_url = data['simplifiedGeometryGeoJSON']
            geojson_response = requests.get(geojson_url)
            
            if geojson_response.status_code == 200:
                # gdf[code] = geojson_data
                gdf = gpd.read_file(geojson_response.content)
                gdf_list.append(gdf)
            else:
                print(f"Failed to download GeoJSON for {code}")
        else:
            print(f"No simplifiedGeometryGeoJSON found for {code}")

    if gdf_list:
        gdf = gpd.GeoDataFrame(pd.concat(gdf_list, ignore_index=True))
        print("Free Churro")
        return gdf.to_json(), gdf
    
    else:
        print("The view from halfway down")

# Country Maps

## Cambodia

### Calculating SA%

In [86]:
cambodia_df = df[df['Country'] == 'Cambodia']
cambodia_df['Store Type'] = cambodia_df['Store Type'].map(store_type)
cambodia_pop = pd.read_excel('data/population_data.xlsx', sheet_name='Cambodia', usecols='A:C')

cambodia_store_count = cambodia_df.groupby(['Country', 'Province', 'Store Type']).size().reset_index(name='Count').pivot_table(
    index=['Country', 'Province'], 
    columns='Store Type', 
    values='Count', 
    fill_value=0
).reset_index()

cambodia_rough = cambodia_store_count.merge(
    multiplier_df,
    on='Country',
    how='left',
    suffixes=('', '_multiplier')
)

cambodia_store_types = [col for col in cambodia_store_count.columns if col not in ['Country', 'Province']]

cambodia_store_count['SA'] = 0
for store in cambodia_store_types:
    if store in multiplier_df.columns:
        cambodia_store_count['SA'] += cambodia_store_count[store] * cambodia_rough[store + '_multiplier']


cambodia_store_count = cambodia_store_count.merge(
    cambodia_pop,
    on=['Country', 'Province'],
    how='left'
)   
cambodia_store_count['SA %'] = cambodia_store_count['SA'] / cambodia_store_count['Population'] * 100
cambodia_store_count['SA %'] = cambodia_store_count['SA %'].fillna(0)

cambodia_store_count['Country'] = cambodia_store_count['Country'].map(country_codes)

latest_date = cambodia_df['Store Launch Date'].max()
latest_date = pd.to_datetime(latest_date).strftime('%Y-%m-%d')
cambodia_store_count

C:\Users\Ethan.loh\AppData\Local\Temp\ipykernel_15012\2156101413.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  cambodia_df['Store Type'] = cambodia_df['Store Type'].map(store_type)


Country              Province  Hospital (not VAH)    RAP  Wholesaler  \
0      KHM            Batdâmbâng                 1.0  180.0         0.0   
1      KHM      Bântéay Méanchey                 0.0   32.0         0.0   
2      KHM             Kaôh Kong                 0.0    1.0         0.0   
3      KHM                   Kep                 0.0    1.0         0.0   
4      KHM          Krong Pailin                 0.0    4.0         0.0   
5      KHM  Krong Preah Sihanouk                 1.0   50.0         0.0   
6      KHM               Krâchéh                 0.0  105.0         0.0   
7      KHM          Kâmpóng Cham                 1.0   60.0         0.0   
8      KHM       Kâmpóng Chhnang                 0.0    3.0         0.0   
9      KHM           Kâmpóng Spœ                 0.0   57.0         0.0   
10     KHM          Kâmpóng Thum                 0.0   68.0         0.0   
11     KHM                Kâmpôt                 0.0   16.0         0.0   
12     KHM                Kândal                 1.0   29.0         0.0   
13     KHM           Môndól Kiri                 0.0   22.0         0.0   
14     KHM       Otdar Mean Chey                 0.0    2.0         0.0   
15     KHM            Phnom Penh                 5.0   98.0         0.0   
16     KHM             Pouthisat                 0.0   25.0         0.0   
17     KHM          Preah Vihéar                 1.0    5.0         0.0   
18     KHM             Prey Vêng                 1.0  115.0         0.0   
19     KHM            Rôtânôkiri                 0.0    3.0         0.0   
20     KHM              Siemréab                 3.0  160.0         0.0   
21     KHM           Stœng Trêng                 0.0   22.0         0.0   
22     KHM            Svay Rieng                 0.0   91.0         0.0   
23     KHM                 Takêv                 1.0    2.0         0.0   
24     KHM           Tbong Khmum                 0.0   97.0         1.0   

           SA    Population        SA %  
0   1080000.0  1.128404e+06   95.710401  
1    192000.0  9.753133e+05   19.685981  
2      6000.0  4.828004e+04   12.427496  
3      6000.0  1.424717e+05    4.211364  
4     24000.0  1.043489e+05   22.999757  
5    300000.0  3.123667e+05   96.040969  
6    630000.0  4.240756e+05  148.558417  
7    360000.0  1.018210e+06   35.356153  
8     18000.0  5.963878e+05    3.018171  
9    342000.0  9.930117e+05   34.440682  
10   408000.0  7.712460e+05   52.901407  
11    96000.0  6.719814e+05   14.286110  
12   174000.0  1.359718e+06   12.796769  
13   132000.0  8.499731e+04  155.299034  
14    12000.0  2.582273e+06    0.464707  
15   588000.0  3.508798e+05  167.578741  
16   150000.0  2.883642e+05   52.017559  
17    30000.0  1.196924e+06    2.506425  
18   690000.0  4.752209e+05  145.195643  
19    18000.0  2.460715e+05    7.314948  
20   960000.0  1.147715e+06   83.644467  
21   132000.0  1.875221e+05   70.391707  
22   546000.0  5.946564e+05   91.817730  
23    12000.0  8.790792e+05    1.365065  
24   582000.0  1.019481e+06   57.087864

In [87]:
latest_date

'2023-11-29'

### Geojson Prep

In [60]:
geojson_data, geojson_df = get_geojsons(['KHM'])

cambodia_province_dict = {
    'Battambang': 'Batdâmbâng',
    'Bantey Meanchey': 'Bântéay Méanchey',
    'Koh Kong': 'Kaôh Kong',
    'Kep': 'Kep',
    'Pailin': 'Krong Pailin',
    'Preah Sihanouk': 'Krong Preah Sihanouk',
    'Kratie': 'Krâchéh',
    'Kampong Cham': 'Kâmpóng Cham',
    'Kampong Chhnang': 'Kâmpóng Chhnang',
    'Kampong Speu': 'Kâmpóng Spœ',
    'Kampong Thom': 'Kâmpóng Thum',
    'Kampot': 'Kâmpôt',
    'Kandal': 'Kândal',
    'Mondulkiri': 'Môndól Kiri',  
    'Oddar Meanchey': 'Otdar Mean Chey',
    'Phnom Penh': 'Phnom Penh',
    'Pursat': 'Pouthisat',
    'Preah Vihear': 'Preah Vihéar',
    'Prey Veng': 'Prey Vêng',
    'Ratanakiri Province': 'Rôtânôkiri',
    'Siem Reap': 'Siemréab',
    'Stung Treng': 'Stœng Trêng',
    'Svay Rieng': 'Svay Rieng',
    'Takeo': 'Takêv',
    'Tbong Khmum': 'Tbong Khmum',
}   

geojson_df['shapeName'] = geojson_df['shapeName'].map(cambodia_province_dict)

geojson_df = geojson_df.merge(
    cambodia_store_count[['Country', 'Province', 'SA %']],
    left_on=['shapeName', 'shapeGroup'],
    right_on=['Province', 'Country'],
    how='left'
)

geojson_df['SA %'] = geojson_df['SA %'].fillna(0)

geojson_df['SA %'] = geojson_df['SA %'].map(lambda x: f"{x:.5g}")
geojson_data = geojson_df.to_json()
geojson_data

present_store_types = cambodia_df['Store Type'].unique()

geojson_df

Free Churro


shapeName shapeISO                  shapeID shapeGroup  \
0            Stœng Trêng    KH-19  37992800B90729700897308        KHM   
1           Preah Vihéar    KH-13  37992800B94509217911919        KHM   
2           Kâmpóng Thum     KH-6  37992800B59838984331544        KHM   
3             Phnom Penh    KH-12  37992800B83627159640807        KHM   
4              Kaôh Kong     KH-9  37992800B81044157598883        KHM   
5                    Kep    KH-23  37992800B18832544789315        KHM   
6                 Kâmpôt     KH-7  37992800B68844415613683        KHM   
7                  Takêv    KH-21  37992800B77204168518017        KHM   
8                 Kândal     KH-8  37992800B57023840568534        KHM   
9              Pouthisat    KH-15  37992800B18682012537966        KHM   
10            Rôtânôkiri    KH-16   37992800B4485162085463        KHM   
11       Kâmpóng Chhnang     KH-4  37992800B66153290508063        KHM   
12          Krong Pailin    KH-24   37992800B9891185734672        KHM   
13      Bântéay Méanchey     KH-1  37992800B60639331187871        KHM   
14              Siemréab    KH-17   37992800B4812755629120        KHM   
15       Otdar Mean Chey    KH-22  37992800B73119019658513        KHM   
16          Kâmpóng Cham     KH-3  37992800B62393256715912        KHM   
17           Môndól Kiri    KH-11  37992800B84760754839946        KHM   
18               Krâchéh    KH-10  37992800B82444097829687        KHM   
19             Prey Vêng    KH-14  37992800B42158555562772        KHM   
20           Kâmpóng Spœ     KH-5  37992800B46036584412355        KHM   
21            Svay Rieng    KH-20    37992800B528078583451        KHM   
22  Krong Preah Sihanouk    KH-18  37992800B48601233133149        KHM   
23           Tbong Khmum    KH-25  37992800B90014860566901        KHM   
24            Batdâmbâng     KH-2  37992800B82526494497621        KHM   

   shapeType                                           geometry Country  \
0       ADM1  POLYGON ((105.89925 13.93708, 105.89391 13.931...     KHM   
1       ADM1  POLYGON ((105.89925 13.93708, 105.8939 13.9479...     KHM   
2       ADM1  POLYGON ((105.53764 13.44956, 105.53262 13.445...     KHM   
3       ADM1  POLYGON ((104.71266 11.57403, 104.71415 11.572...     KHM   
4       ADM1  MULTIPOLYGON (((103.18634 10.83308, 103.18335 ...     KHM   
5       ADM1  MULTIPOLYGON (((104.32306 10.44403, 104.32255 ...     KHM   
6       ADM1  POLYGON ((104.41631 10.4456, 104.41559 10.4439...     KHM   
7       ADM1  POLYGON ((104.71334 10.53123, 104.75407 10.517...     KHM   
8       ADM1  POLYGON ((105.03761 10.89616, 105.04077 10.896...     KHM   
9       ADM1  POLYGON ((104.17348 12.77205, 103.87467 13.089...     KHM   
10      ADM1  POLYGON ((106.60811 13.32283, 106.74592 13.227...     KHM   
11      ADM1  POLYGON ((104.38279 12.5775, 104.38734 12.5129...     KHM   
12      ADM1  POLYGON ((102.48643 12.98076, 102.48606 12.976...     KHM   
13      ADM1  POLYGON ((103.03187 14.25023, 103.03317 14.239...     KHM   
14      ADM1  POLYGON ((104.42202 13.93901, 104.41953 13.935...     KHM   
15      ADM1  POLYGON ((104.4672 14.34532, 104.46325 14.3451...     KHM   
16      ADM1  POLYGON ((104.87226 12.23941, 104.87372 12.232...     KHM   
17      ADM1  POLYGON ((106.34991 13.40047, 106.35149 13.389...     KHM   
18      ADM1  POLYGON ((105.58902 13.23035, 105.58721 13.216...     KHM   
19      ADM1  POLYGON ((105.18749 10.91159, 105.19745 10.911...     KHM   
20      ADM1  POLYGON ((104.0416 11.43604, 104.04101 11.4331...     KHM   
21      ADM1  POLYGON ((105.61357 10.97373, 105.6677 10.9876...     KHM   
22      ADM1  MULTIPOLYGON (((102.88027 9.93098, 102.88302 9...     KHM   
23      ADM1  POLYGON ((105.41827 11.82689, 105.4189 11.8221...     KHM   
24      ADM1  POLYGON ((103.87467 13.08995, 103.70895 13.261...     KHM   

                Province     SA %  
0            Stœng Trêng   70.392  
1           Preah Vihéar   2.5064  
2           Kâmpóng Thum   52.901  
3             Phnom P

### Map Making

In [88]:
sa_dict = cambodia_store_count.groupby("Province")["SA %"].max().to_dict()

map = folium.Map(
    location=[12.5657, 104.9910], 
    zoom_start=7
)

folium.TileLayer(
    tiles='https://mt1.google.com/vt/lyrs=m&x={x}&y={y}&z={z}',
    attr='Google',
    name='Google Maps'  
).add_to(map)

folium.GeoJson(
    geojson_data,
    style_function=lambda feature: {
        "fillColor": linear(min(sa_dict.get(feature["properties"]["shapeName"], 0), 100)),
        "color": "black",
        "weight": 1,
        "fillOpacity": 0.6,
    },
    tooltip=folium.GeoJsonTooltip(
        fields=["shapeName", 'SA %'],
        aliases=["Region:", 'SA %'],
    ),
    control=False,
).add_to(map)

linear.caption = "SA % (0–100 scale)"
linear.add_to(map)

for store in present_store_types:
    make_points(cambodia_df, store, map)

store_colors = {
    store_type: get_store_type_color(store_type)
    for store_type in present_store_types
}

legend_items = ''.join([
    f'<i style="background:{color}; width:10px; height:10px; display:inline-block; margin-right:5px;"></i>{long_name}<br>'
    for long_name, color in store_colors.items()
])

legend_html = """
{% macro html(this, kwargs) %}
<div style="
    position: fixed;
    bottom: 50px;
    left: 50px;
    width: 300px;
    background-color: white;
    border:2px solid grey;
    z-index:9999;
    font-size:14px;
    padding: 10px;
    border-radius: 5px;
">
    <b>Store Type Legend</b><br>
    """ + legend_items + """
</div>
{% endmacro %}
"""

legend = MacroElement()
legend._template = Template(legend_html)
map.add_child(legend)

date_html = f"""
{% macro html(this, kwargs) %}
<div style="
    position: fixed;
    top: 10px;
    left: 10px;
    width: auto;
    background-color: white;
    border: 2px solid grey;
    border-radius: 5px;
    z-index:9999;
    font-size:14px;
    padding: 8px 12px;
    box-shadow: 2px 2px 5px rgba(0,0,0,0.3);
">
    <b>Data Date:</b> {date_str}
</div>
{% endmacro %}
"""

date_box = MacroElement()
date_box._template = Template(date_html)
map.add_child(date_box)


folium.LayerControl().add_to(map)


SyntaxError: f-string: invalid syntax (2241365486.py, line 70)

In [62]:
map.save('assets/Cambodia_map.html')

## Bangladesh

### Calculating SA%

In [63]:
bangladesh_df = df[df['Country'] == 'Bangladesh']

bangladesh_df['Store Type'] = bangladesh_df['Store Type'].map(store_type)

bangladesh_pop = pd.read_excel('data/population_data.xlsx', sheet_name='Bangladesh', usecols='A:C')

bangladesh_store_count = bangladesh_df.groupby(['Country', 'Province', 'Store Type']).size().reset_index(name='Count').pivot_table(
    index=['Country', 'Province'], 
    columns='Store Type', 
    values='Count', 
    fill_value=0
).reset_index()

bangladesh_rough = bangladesh_store_count.merge(
    multiplier_df,
    on='Country',
    how='left',
    suffixes=('', '_multiplier')
)

bangladesh_store_types = [col for col in bangladesh_store_count.columns if col not in ['Country', 'Province']]

bangladesh_store_count['SA'] = 0
for store in bangladesh_store_types:
    if (store in multiplier_df.columns) & (store != 'VAH') & (store != 'VC'):
        bangladesh_store_count['SA'] += bangladesh_store_count[store] * bangladesh_rough[store + '_multiplier']


bangladesh_store_count = bangladesh_store_count.merge(
    bangladesh_pop,
    on=['Country', 'Province'],
    how='left'
)   

bangladesh_store_count['SA %'] = bangladesh_store_count['SA'] / bangladesh_store_count['Population'] * 100
bangladesh_store_count['SA %'] = bangladesh_store_count['SA %'].fillna(0)

bangladesh_store_count['Country'] = bangladesh_store_count['Country'].map(country_codes)
bangladesh_store_count


C:\Users\Ethan.loh\AppData\Local\Temp\ipykernel_15012\555097642.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  bangladesh_df['Store Type'] = bangladesh_df['Store Type'].map(store_type)


Country    Province   EP  FRE (MMO, EMO, EM, ER)  Hospital (not VAH)  \
0     BGD     Barisal  0.0                    11.0                 3.0   
1     BGD  Chittagong  0.0                   136.0                23.0   
2     BGD       Dhaka  0.0                   163.0                48.0   
3     BGD      Khulna  2.0                   239.0                10.0   
4     BGD  Mymensingh  1.0                    82.0                 5.0   
5     BGD    Rajshahi  0.0                   258.0                11.0   
6     BGD     Rangpur  0.0                   174.0                14.0   
7     BGD      Sylhet  0.0                    10.0                12.0   

   Retail  VAH         SA    Population       SA %  
0     0.0  0.0   280500.0  9.530835e+06   2.943079  
1    14.0  5.0  3468000.0  3.492998e+07   9.928434  
2    19.0  5.0  4156500.0  4.664802e+07   8.910346  
3    26.0  1.0  6145500.0  1.820482e+07  33.757549  
4    11.0  1.0  2116500.0  1.291529e+07  16.387554  
5     9.0  2.0  6579000.0  2.125115e+07  30.958329  
6     0.0  4.0  4437000.0  1.841622e+07  24.092896  
7    14.0  3.0   255000.0  1.166606e+07   2.185828

### Geojson Prep

In [64]:
geojson_data, geojson_df = get_geojsons(['BGD'])

bangladesh_province_dict = {
    'Dhaka': 'Dhaka',
    'Chattogram': 'Chattogram',
    'Khulna': 'Khulna',
    'Rajshani': 'Rajshahi', # Rajshani is a misspelling of Rajshahi
    'Barishal': 'Barishal',
    'Sylhet': 'Sylhet',
    'Rangpur': 'Rangpur',
    'Mymensingh': 'Mymensingh',
}

geojson_df['shapeName'] = geojson_df['shapeName'].map(bangladesh_province_dict)

geojson_df = geojson_df.merge(
    bangladesh_store_count[['Country', 'Province', 'SA %']],
    left_on=['shapeName', 'shapeGroup'],
    right_on=['Province', 'Country'],
    how='left'
)

geojson_df['SA %'] = geojson_df['SA %'].fillna(0)

geojson_df['SA %'] = geojson_df['SA %'].map(lambda x: f"{x:.5g}")
geojson_data = geojson_df.to_json()

present_store_types = bangladesh_df['Store Type'].unique()

geojson_df

Free Churro


shapeName shapeISO                  shapeID shapeGroup shapeType  \
0         NaN     BD-B  32408957B94023193097291        BGD      ADM1   
1       Dhaka     BD-C  32408957B77718829177955        BGD      ADM1   
2  Mymensingh     BD-H  32408957B83626866084602        BGD      ADM1   
3    Rajshahi     BD-E  32408957B27409320841034        BGD      ADM1   
4     Rangpur     BD-F  32408957B77489436868882        BGD      ADM1   
5      Sylhet     BD-G  32408957B58397560032916        BGD      ADM1   
6      Khulna     BD-D   32408957B3859287816056        BGD      ADM1   
7         NaN     BD-A  32408957B31852228482374        BGD      ADM1   

                                            geometry Country    Province  \
0  MULTIPOLYGON (((92.31408 20.66637, 92.30003 20...     NaN         NaN   
1  POLYGON ((91.21485 24.24363, 91.20059 24.2823,...     BGD       Dhaka   
2  POLYGON ((91.1939 24.63997, 91.19779 24.6418, ...     BGD  Mymensingh   
3  POLYGON ((89.79949 24.57915, 89.79711 24.65209...     BGD    Rajshahi   
4  POLYGON ((89.79002 25.39089, 89.82697 25.35564...     BGD     Rangpur   
5  POLYGON ((91.2954 24.00349, 91.3187 23.99949, ...     BGD      Sylhet   
6  MULTIPOLYGON (((89.35718 21.6887, 89.36168 21....     BGD      Khulna   
7  MULTIPOLYGON (((90.55128 21.84717, 90.55848 21...     NaN         NaN   

     SA %  
0       0  
1  8.9103  
2  16.388  
3  30.958  
4  24.093  
5  2.1858  
6  33.758  
7       0

### Map Making

In [65]:
sa_dict = bangladesh_store_count.groupby("Province")["SA %"].max().to_dict()

map = folium.Map(
    location=[23.6850, 90.3563], 
    zoom_start=7
)

folium.TileLayer(
    tiles='https://mt1.google.com/vt/lyrs=m&x={x}&y={y}&z={z}',
    attr='Google',
    name='Google Maps'  
).add_to(map)

folium.GeoJson(
    geojson_data,
    style_function=lambda feature: {
        "fillColor": linear(min(sa_dict.get(feature["properties"]["shapeName"], 0), 100)),
        "color": "black",
        "weight": 1,
        "fillOpacity": 0.6,
    },
    tooltip=folium.GeoJsonTooltip(
        fields=["shapeName", 'SA %'],
        aliases=["Region:", 'SA %'],
    ),
    control=False,
).add_to(map)

linear.caption = "SA % (0–100 scale)"
linear.add_to(map)

for store in present_store_types:
    make_points(bangladesh_df, store, map)

store_colors = {
    store_type: get_store_type_color(store_type)
    for store_type in present_store_types
}

legend_items = ''.join([
    f'<i style="background:{color}; width:10px; height:10px; display:inline-block; margin-right:5px;"></i>{long_name}<br>'
    for long_name, color in store_colors.items()
])

legend_html = """
{% macro html(this, kwargs) %}
<div style="
    position: fixed;
    bottom: 50px;
    left: 50px;
    width: 300px;
    background-color: white;
    border:2px solid grey;
    z-index:9999;
    font-size:14px;
    padding: 10px;
    border-radius: 5px;
">
    <b>Store Type Legend</b><br>
    """ + legend_items + """
</div>
{% endmacro %}
"""

legend = MacroElement()
legend._template = Template(legend_html)
map.add_child(legend)


folium.LayerControl().add_to(map)

In [66]:
map.save('assets/Bangladesh_map.html')

## Indonesia

### Calculating SA%

In [67]:
indonesia_df = df[df['Country'] == 'Indonesia']

indonesia_df['Store Type'] = indonesia_df['Store Type'].map(store_type)
indonesia_pop = pd.read_excel('data/population_data.xlsx', sheet_name='Indonesia', usecols='A:C')

indonesia_store_count = indonesia_df.groupby(['Country', 'Province', 'Store Type']).size().reset_index(name='Count').pivot_table(
    index=['Country', 'Province'], 
    columns='Store Type', 
    values='Count', 
    fill_value=0
).reset_index()

indonesia_rough = indonesia_store_count.merge(
    multiplier_df,
    on='Country',
    how='left',
    suffixes=('', '_multiplier')
)

indonesia_store_types = [col for col in indonesia_store_count.columns if col not in ['Country', 'Province']]

indonesia_store_count['SA'] = 0
for store in indonesia_store_types:
    if (store in multiplier_df.columns) & (store != 'VAH') & (store != 'VC'):
        indonesia_store_count['SA'] += indonesia_store_count[store] * indonesia_rough[store + '_multiplier']


indonesia_store_count = indonesia_store_count.merge(
    indonesia_pop,
    on=['Country', 'Province'],
    how='left'
)   

indonesia_store_count['SA %'] = indonesia_store_count['SA'] / indonesia_store_count['Population'] * 100
indonesia_store_count['SA %'] = indonesia_store_count['SA %'].fillna(0)

indonesia_store_count['Country'] = indonesia_store_count['Country'].map(country_codes)

indonesia_store_count

C:\Users\Ethan.loh\AppData\Local\Temp\ipykernel_15012\2680631880.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  indonesia_df['Store Type'] = indonesia_df['Store Type'].map(store_type)


Country                       Province     EP  FRE (MM)  \
0      IDN                           Aceh   13.0      38.0   
1      IDN                           Bali   14.0      52.0   
2      IDN        Bangka Belitung Islands    1.0       0.0   
3      IDN                         Banten   20.0      59.0   
4      IDN                       Bengkulu    7.0     416.0   
5      IDN                   Central Java    1.0       0.0   
6      IDN             Central Kalimantan    0.0       0.0   
7      IDN               Central Sulawesi    1.0       0.0   
8      IDN     Daerah Istimewa Yogyakarta    1.0       0.0   
9      IDN  Daerah Khusus Ibukota Jakarta   25.0     182.0   
10     IDN                      East Java    6.0       0.0   
11     IDN                      Gorontalo    1.0       0.0   
12     IDN               Ho Chi Minh City    0.0       0.0   
13     IDN                        Jakarta    0.0       0.0   
14     IDN                          Jambi   16.0       0.0   
15     IDN                     Jawa Barat   44.0     488.0   
16     IDN                    Jawa Tengah   25.0     181.0   
17     IDN                     Jawa Timur  117.0     165.0   
18     IDN               Kalimantan Barat    8.0      48.0   
19     IDN             Kalimantan Selatan    7.0       0.0   
20     IDN              Kalimantan Tengah    4.0      33.0   
21     IDN               Kalimantan Timur   17.0      39.0   
22     IDN               Kalimantan Utara    1.0       0.0   
23     IDN      Kepulauan Bangka Belitung    2.0       0.0   
24     IDN                 Kepulauan Riau    3.0       0.0   
25     IDN                        Lampung   15.0     175.0   
26     IDN                         Maluku    3.0       0.0   
27     IDN                   Maluku Utara    2.0       0.0   
28     IDN                Negeri Sembilan    1.0       0.0   
29     IDN                   North Maluku    0.0       0.0   
30     IDN                 North Sulawesi    0.0       0.0   
31     IDN                  North Sumatra    0.0      36.0   
32     IDN            Nusa Tenggara Barat   25.0      87.0   
33     IDN            Nusa Tenggara Timur    1.0       0.0   
34     IDN                    Papua Barat    2.0       0.0   
35     IDN                           Riau   17.0      93.0   
36     IDN               South Kalimantan    1.0       0.0   
37     IDN                 South Sulawesi    0.0       0.0   
38     IDN                  South Sumatra    3.0       0.0   
39     IDN   Special Region of Yogyakarta    0.0      80.0   
40     IDN                 Sulawesi Barat    2.0       0.0   
41     IDN               Sulawesi Selatan   26.0      28.0   
42     IDN                Sulawesi Tengah    4.0       0.0   
43     IDN              Sulawesi Tenggara    4.0       0.0   
44     IDN                 Sulawesi Utara    5.0      16.0   
45     IDN                 Sumatera Barat   13.0     132.0   
46     IDN               Sumatera Selatan   20.0      88.0   
47     IDN                 Sumatera Utara   29.0     135.0   
48     IDN                      West Java    2.0       0.0   
49     IDN                West Kalimantan    0.0       0.0   
50     IDN             West Nusa Tenggara    5.0       0.0   
51     IDN                   West Sumatra    3.0       0.0   

    FRE (MMO, EMO, EM, ER)   RAP  VAH          SA    Population        SA %  
0                      3.0   0.0  0.0   1476000.0  5.534199e+06   26.670526  
1                      6.0   5.0  1.0   1984000.0  4.529660e+06   43.800195  
2                      0.0   0.0  0.0     40000.0           NaN    0.000000  
3                      7.0  19.0  0.0   2530000.0  1.248983e+07   20.256489  
4                      0.0   0.0  0.0   9432000.0  2.109520e+06  447.115844  
5                      6.0   0.0  0.0    280000.0           NaN    0.000000  
6                      1.0   0.0  0.0     40000.0           NaN    0.000000  
7                      0.0   0.0  0.0     40000.0           NaN    0.000000  
8             

### Geojson Prep

In [68]:
geojson_data, geojson_df = get_geojsons(['IDN'])

indonesia_province_dict = {
    "Bali": "Bali",
    "West Nusa Tenggara": "Nusa Tenggara Barat",
    "Banten": "Banten",
    "Central Java": "Jawa Tengah",
    "West Java": "Jawa Barat",
    "Central Kalimantan": "Kalimantan Tengah",
    "South Kalimantan": "Kalimantan Selatan",
    "West Kalimantan": "Kalimantan Barat",
    "Central Sulawesi": "Sulawesi Tengah",
    "Gorontalo": "Gorontalo",
    "North Sulawesi": "Sulawesi Utara",
    "South Sulawesi": "Sulawesi Selatan",
    "Southeast Sulawesi": "Sulawesi Tenggara",
    "West Sulawesi": "Sulawesi Barat",
    "Aceh": "Aceh",
    "Bengkulu": "Bengkulu",
    "Jambi": "Jambi",
    "Lampung": "Lampung",
    "Riau": "Riau",
    "West Sumatra": "Sumatera Barat",
    "South Sumatra": "Sumatera Selatan",
    "North Sumatra": "Sumatera Utara",
    "East Nusa Tenggara": "Nusa Tenggara Timur",
    "Maluku": "Maluku",
    "North Maluku": "Maluku Utara",
    "East Java": "Jawa Timur",
    "Bangka-Belitung Islands": "Kepulauan Bangka Belitung",
    "Riau Islands": "Kepulauan Riau",
    "Papua": "Papua",
    "West Papua": "Papua Barat",
    "East Kalimantan": "Kalimantan Timur",
    "North Kalimantan": "Kalimantan Utara",
    "Special Region of Yogyakarta": "Daerah Istimewa Yogyakarta",
    "Jakarta Special Capital Region": "Daerah Khusus Ibukota Jakarta"
}


geojson_df['shapeName'] = geojson_df['shapeName'].map(indonesia_province_dict)

geojson_df = geojson_df.merge(
    indonesia_store_count[['Country', 'Province', 'SA %']],
    left_on=['shapeName', 'shapeGroup'],
    right_on=['Province', 'Country'],
    how='left'
)

geojson_df['SA %'] = geojson_df['SA %'].fillna(0)

geojson_df['SA %'] = geojson_df['SA %'].map(lambda x: f"{x:.5g}")
geojson_data = geojson_df.to_json()
geojson_data

present_store_types = indonesia_df['Store Type'].unique()

geojson_df

Free Churro


shapeName shapeISO                  shapeID  \
0                            Bali    ID-BA   65028918B6690755070061   
1             Nusa Tenggara Barat    ID-NB  65028918B98829509874887   
2                          Banten    ID-BT  65028918B99918739720671   
3                     Jawa Tengah    ID-JT  65028918B13838862025135   
4                      Jawa Barat    ID-JB  65028918B28366581005022   
5               Kalimantan Tengah    ID-KT  65028918B28198720309323   
6              Kalimantan Selatan    ID-KS  65028918B30993740608215   
7                Kalimantan Barat    ID-KB  65028918B19721185942402   
8                 Sulawesi Tengah    ID-ST  65028918B55787629749874   
9                       Gorontalo    ID-GO  65028918B94020759558104   
10                 Sulawesi Utara    ID-SA  65028918B26897900130576   
11               Sulawesi Selatan    ID-SN  65028918B17554737605304   
12              Sulawesi Tenggara    ID-SG  65028918B94007491868798   
13                 Sulawesi Barat    ID-SR  65028918B46678513676023   
14                           Aceh    ID-AC  65028918B93184959873838   
15                       Bengkulu    ID-BE  65028918B30999004822283   
16                          Jambi    ID-JA  65028918B29194895292819   
17                        Lampung    ID-LA  65028918B88589358118692   
18                           Riau    ID-RI  65028918B11286430647546   
19                 Sumatera Barat    ID-SB   65028918B4119458748300   
20               Sumatera Selatan    ID-SS   65028918B9551391119865   
21                 Sumatera Utara    ID-SU  65028918B37605681672150   
22            Nusa Tenggara Timur    ID-NT  65028918B90323071856071   
23                         Maluku    ID-MA  65028918B48178230554278   
24                   Maluku Utara    ID-MU  65028918B51364455052819   
25                     Jawa Timur    ID-JI  65028918B43243108525571   
26      Kepulauan Bangka Belitung    ID-BB  65028918B10722647473585   
27                 Kepulauan Riau    ID-KR  65028918B90123187256494   
28                          Papua    ID-PA  65028918B16658067687714   
29                    Papua Barat    ID-PB  65028918B84835514626455   
30               Kalimantan Timur    ID-KI  65028918B68445169823185   
31               Kalimantan Utara    ID-KU  65028918B52923737893214   
32     Daerah Istimewa Yogyakarta    ID-YO   65028918B6070530336190   
33  Daerah Khusus Ibukota Jakarta    ID-JK  65028918B14696209246677   

   shapeGroup shapeType                                           geometry  \
0         IDN      ADM1  MULTIPOLYGON (((114.5197 -8.1, 114.52752 -8.09...   
1         IDN      ADM1  MULTIPOLYGON (((119.23765 -8.66347, 119.23498 ...   
2         IDN      ADM1  MULTIPOLYGON (((105.53122 -7.03135, 105.53102 ...   
3         IDN      ADM1  MULTIPOLYGON (((108.88484 -6.80937, 108.88532 ...   
4         IDN      ADM1  POLYGON ((106.39563 -6.98024, 106.4008 -6.9773...   
5         IDN      ADM1  MULTIPOLYGON (((113.36649 -3.30172, 113.37216 ...   
6         IDN      ADM1  MULTIPOLYGON (((117.05853 -5.10152, 117.06175 ...   
7         IDN      ADM1  MULTIPOLYGON (((109.28228 -0.61361, 109.28863 ...   
8         IDN      ADM1  MULTIPOLYGON (((123.66903 -2.16135, 123.66466 ...   
9         IDN      ADM1  MULTIPOLYGON (((122.85535 0.89565, 122.85601 0...   
10        IDN      ADM1  MULTIPOLYGON (((125.22053 1.43814, 125.21871 1...   
11        IDN      ADM1  MULTIPOLYGON (((121.77106 -7.26502, 121.76667 ...   
12        IDN      ADM1  MULTIPOLYGON (((122.71163 -6.21305, 122.72039 ...   
13        IDN      ADM1  MULTIPOLYGON (((119.37094 -3.46772, 119.36304 ...   
14        IDN      ADM1  MULTIPOLYGON (((97.07716 2.0791, 97.08299 2.06...   
15        IDN      ADM1  MULTIPOLYGON (((102.08789 -5.3566, 102.10154 -...   
16        IDN      ADM1  MULTIPOLYGON (((102.06342 -2.77043, 102.06347 ...   
17        IDN      ADM1  MULTIPOLYGON (((105.45701 -6.13513, 105.45574 ...   
18        IDN      ADM1  MULTIPOLYGON (((103.09059 0.791

### Map Making

In [69]:
sa_dict = indonesia_store_count.groupby("Province")["SA %"].max().to_dict()

map = folium.Map(
    location=[-2.5489, 118.0149], 
    zoom_start=5
)

folium.TileLayer(
    tiles='https://mt1.google.com/vt/lyrs=m&x={x}&y={y}&z={z}',
    attr='Google',
    name='Google Maps'  
).add_to(map)

folium.GeoJson(
    geojson_data,
    style_function=lambda feature: {
        "fillColor": linear(min(sa_dict.get(feature["properties"]["shapeName"], 0), 100)),
        "color": "black",
        "weight": 1,
        "fillOpacity": 0.6,
    },
    tooltip=folium.GeoJsonTooltip(
        fields=["shapeName", 'SA %'],
        aliases=["Region:", 'SA %'],
    ),
    control=False,
).add_to(map)

linear.caption = "SA % (0–100 scale)"
linear.add_to(map)

for store in present_store_types:
    make_points(indonesia_df, store, map)

store_colors = {
    store_type: get_store_type_color(store_type)
    for store_type in present_store_types
}

legend_items = ''.join([
    f'<i style="background:{color}; width:10px; height:10px; display:inline-block; margin-right:5px;"></i>{long_name}<br>'
    for long_name, color in store_colors.items()
])

legend_html = """
{% macro html(this, kwargs) %}
<div style="
    position: fixed;
    bottom: 50px;
    left: 50px;
    width: 300px;
    background-color: white;
    border:2px solid grey;
    z-index:9999;
    font-size:14px;
    padding: 10px;
    border-radius: 5px;
">
    <b>Store Type Legend</b><br>
    """ + legend_items + """
</div>
{% endmacro %}
"""

legend = MacroElement()
legend._template = Template(legend_html)
map.add_child(legend)


folium.LayerControl().add_to(map)
map

In [70]:
map.save('assets/Indonesia_map.html')

## India

### Calculating SA%

In [71]:
india_df = df[df['Country'] == 'India']

india_df['Store Type'] = india_df['Store Type'].map(store_type)
india_pop = pd.read_excel('data/population_data.xlsx', sheet_name='India', usecols='A:C')

india_store_count = india_df.groupby(['Country', 'Province', 'Store Type']).size().reset_index(name='Count').pivot_table(
    index=['Country', 'Province'], 
    columns='Store Type', 
    values='Count', 
    fill_value=0
).reset_index()

india_rough = india_store_count.merge(
    multiplier_df,
    on='Country',
    how='left',
    suffixes=('', '_multiplier')
)


india_store_types = [col for col in india_store_count.columns if col not in ['Country', 'Province']]

india_store_count['SA'] = 0
for store in india_store_types:
    if (store in multiplier_df.columns) & (store != 'VAH') & (store != 'VC'):
        india_store_count['SA'] += india_store_count[store] * india_rough[store + '_multiplier']


india_store_count = india_store_count.merge(
    india_pop,
    on=['Country', 'Province'],
    how='left'
)   

india_store_count['SA %'] = india_store_count['SA'] / india_store_count['Population'] * 100
india_store_count['SA %'] = india_store_count['SA %'].fillna(0)

india_store_count['Country'] = india_store_count['Country'].map(country_codes)

india_store_count

C:\Users\Ethan.loh\AppData\Local\Temp\ipykernel_15012\1305470770.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  india_df['Store Type'] = india_df['Store Type'].map(store_type)


Country           Province     EP  FRE (MMO, EMO, EM, ER)  \
0      IND     Andhra Pradesh  151.0                    68.0   
1      IND              Assam   25.0                     5.0   
2      IND              Bihar   43.0                   118.0   
3      IND         Chandigarh    1.0                     0.0   
4      IND       Chhattisgarh  103.0                     7.0   
5      IND                Goa   26.0                     0.0   
6      IND            Gujarat  124.0                     6.0   
7      IND            Haryana   49.0                    54.0   
8      IND   Himachal Pradesh   16.0                     2.0   
9      IND  Jammu and Kashmir    0.0                     2.0   
10     IND          Jharkhand    0.0                     2.0   
11     IND          Karnataka  186.0                   388.0   
12     IND             Kerala    0.0                     0.0   
13     IND     Madhya Pradesh  247.0                   857.0   
14     IND        Maharashtra   24.0                   753.0   
15     IND            Manipur    0.0                     0.0   
16     IND          Meghalaya    0.0                     0.0   
17     IND            Mizoram    3.0                     0.0   
18     IND       NCT of Delhi    6.0                    26.0   
19     IND           Nagaland    3.0                     0.0   
20     IND             Odisha   35.0                   255.0   
21     IND             Punjab   69.0                    14.0   
22     IND          Rajasthan   41.0                  1194.0   
23     IND             Sikkim    1.0                     0.0   
24     IND         Tamil Nadu    0.0                    13.0   
25     IND          Telangana    1.0                   152.0   
26     IND      Uttar Pradesh  164.0                  4754.0   
27     IND        Uttarakhand   25.0                    44.0   
28     IND        West Bengal   80.0                   289.0   

    Hospital (not VAH)  Mobile Unit    RAP  Retail  Wholesaler/Distributor  \
0                  0.0          0.0    3.0     0.0                     0.0   
1                 15.0          0.0    2.0     0.0                     0.0   
2                 29.0          1.0    0.0     0.0                     0.0   
3                  0.0          0.0    0.0     0.0                     0.0   
4                  3.0          0.0    0.0    10.0                     1.0   
5                  0.0          0.0    0.0     0.0                     0.0   
6                 20.0          0.0    2.0     0.0                     0.0   
7                  4.0          0.0    4.0     0.0                     0.0   
8                  0.0          0.0    1.0     0.0                     0.0   
9                  0.0          0.0    0.0     0.0                     0.0   
10                 4.0          0.0    0.0     0.0                     0.0   
11               166.0          6.0    0.0     0.0                     0.0   
12                 2.0          0.0    4.0     0.0                     0.0   
13                59.0          1.0    4.0     3.0                     0.0   
14                41.0          3.0  172.0     0.0                     0.0   
15                 2.0          0.0    0.0     0.0                     0.0   
16                 0.0          1.0    0.0     0.0                     0.0   
17                 0.0          0.0    0.0     0.0                     0.0   
18                 2.0          0.0   13.0     0.0                     0.0   
19                 0.0          0.0    0.0     0.0                     0.0   
20                29.0          0.0    0.0     4.0                     0.0   
21                14.0          0.0    0.0     0.0                     0.0   
22                44.0          0.0    1.0     2.0                     0.0   
23                 0.0          0.0    0.0     0.0                     0.0   
24                 0.0          3.0    3.0     0.0                     0.0   
25                55.0          2.0    0.0     0.0    

### Geojson Prep

In [72]:
geojson_india, geojson_df = get_geojsons(['IND'])

india_province_dict = {
    'Puducherry': 'Puducherry',
    'Bihār': 'Bihar',
    'Chandīgarh': 'Chandigarh',
    'Chhattīsgarh': 'Chhattisgarh',
    'Delhi': 'NCT of Delhi',
    'Gujarāt': 'Gujarat',
    'Haryāna': 'Haryana',
    'Himāchal Pradesh': 'Himachal Pradesh',
    'Jhārkhand': 'Jharkhand',
    'Karnātaka': 'Karnataka',
    'Ladākh': 'Ladakh',
    'Mahārāshtra': 'Maharashtra',
    'Meghālaya': 'Meghalaya',
    'Nāgāland': 'Nagaland',
    'Rājasthān': 'Rajasthan',
    'Tamil Nādu': 'Tamil Nadu',
    'Telangāna': 'Telangana',
    'Uttarākhand': 'Uttarakhand',
}

geojson_df['shapeName'] = geojson_df['shapeName'].apply(
    lambda x: india_province_dict[x] if x in india_province_dict else x
)

geojson_df = geojson_df.merge(
    india_store_count[['Country', 'Province', 'SA %']],
    left_on=['shapeName', 'shapeGroup'],
    right_on=['Province', 'Country'],
    how='left'
)

geojson_df['SA %'] = geojson_df['SA %'].fillna(0)

geojson_df['SA %'] = geojson_df['SA %'].map(lambda x: f"{x:.5g}")
geojson_data = geojson_df.to_json()

present_store_types = india_df['Store Type'].unique()

geojson_df

Free Churro


shapeName shapeISO                 shapeID  \
0                                 Puducherry    IN-PY  1811400B81659894240990   
1                                Maharashtra    IN-MH  1811400B15614733245507   
2                                   Nagaland    IN-NL  1811400B74762431478096   
3                                Lakshadweep    IN-LD  1811400B55669546485086   
4                              Uttar Pradesh    IN-UP  1811400B11231190780494   
5                                 Tamil Nadu    IN-TN  1811400B21167269026319   
6                               Chhattisgarh    IN-CT  1811400B70654311394581   
7                                    Gujarat    IN-GJ  1811400B80305611676067   
8                               NCT of Delhi    IN-DL  1811400B23625213884851   
9                                     Sikkim    IN-SK  1811400B15456792557830   
10                                   Tripura    IN-TR  1811400B57209440839078   
11                               West Bengal    IN-WB  1811400B32673734874058   
12                                    Odisha    IN-OR  1811400B82358585030651   
13                                     Bihar    IN-BR  1811400B26595099860318   
14                                    Ladakh    IN-LA  1811400B23769854471902   
15                                 Rajasthan    IN-RJ  1811400B37341166588993   
16                                 Telangana    IN-TG  1811400B25711494603400   
17                            Andhra Pradesh    IN-AP  1811400B84418948762846   
18                                   Mizoram    IN-MZ  1811400B49281905528064   
19                         Arunāchal Pradesh    IN-AR  1811400B16134215155042   
20                                 Meghalaya    IN-ML  1811400B28404458933503   
21                                 Jharkhand    IN-JH  1811400B52412412689061   
22                                     Assam    IN-AS  1811400B78322693766699   
23                                   Manipur    IN-MN  1811400B97532436596698   
24                                 Karnataka    IN-KA  1811400B56841107211215   
25                               Uttarakhand    IN-UT   1811400B3558497485804   
26  Dādra and Nagar Haveli and Damān and Diu    IN-DH  1811400B51283975314925   
27                            Madhya Pradesh    IN-MP  1811400B75807316846587   
28                                       Goa    IN-GA   1811400B6111924962807   
29                                    Kerala    IN-KL  1811400B45534780755480   
30                                Chandigarh    IN-CH  1811400B77692474244036   
31               Andaman and Nicobar Islands    IN-AN  1811400B21325138943523   
32                          Himachal Pradesh    IN-HP  1811400B21086746745937   
33                         Jammu and Kashmīr    IN-JK  1811400B42025667129192   
34                                    Punjab    IN-PB  1811400B91946361694107   
35                                   Haryana    IN-HR  1811400B68407848780347   

   shapeGroup shapeType                                           geometry  \
0         IND      ADM1  MULTIPOLYGON (((75.53056 11.70403, 75.5301 11....   
1         IND      ADM1  MULTIPOLYGON (((80.27289 18.72299, 80.25927 18...   
2         IND      ADM1  POLYGON ((95.23392 26.68246, 95.23018 26.694, ...   
3         IND      ADM1  MULTIPOLYGON (((73.01113 8.27759, 73.01026 8.2...   
4         IND      ADM1  MULTIPOLYGON (((79.39526 25.03209, 79.40181 25...   
5         IND      ADM1  MULTIPOLYGON (((79.48966 9.12061, 79.48883 9.1...   
6         IND      ADM1  POLYGON ((80.27289 18.72299, 80.27844 18.72164...   
7         IND      ADM1  MULTIPOLYGON (((71.15113 20.76011, 71.15117 20...   
8         IND      ADM1  POLYGON ((77.20984 28.85787, 77.19768 28.85926...   
9         IND      ADM1  POLYGON ((88.01482 27.21171, 88.02142 27.21783...   
10        IND      ADM1  POLYGON ((91.81543 23.50429, 91.82239 23.49873...   
11        IND      ADM1  MULTIPOLYGON (((88.21501 21.49303, 88.22884 21...   
12        IND      ADM1

### Map Making

In [73]:
sa_dict = india_store_count.groupby("Province")["SA %"].max().to_dict()

map = folium.Map(
    location=[22.9734, 78.6569], 
    zoom_start=5
)

folium.TileLayer(
    tiles='https://mt1.google.com/vt/lyrs=m&x={x}&y={y}&z={z}',
    attr='Google',
    name='Google Maps'  
).add_to(map)

folium.GeoJson(
    geojson_data,
    style_function=lambda feature: {
        "fillColor": linear(min(sa_dict.get(feature["properties"]["shapeName"], 0), 100)),
        "color": "black",
        "weight": 1,
        "fillOpacity": 0.6,
    },
    tooltip=folium.GeoJsonTooltip(
        fields=["shapeName", 'SA %'],
        aliases=["Region:", 'SA %'],
    ),
    control=False,
).add_to(map)

linear.caption = "SA % (0–100 scale)"
linear.add_to(map)

for store in present_store_types:
    make_points(india_df, store, map)

store_colors = {
    store_type: get_store_type_color(store_type)
    for store_type in present_store_types
}

legend_items = ''.join([
    f'<i style="background:{color}; width:10px; height:10px; display:inline-block; margin-right:5px;"></i>{long_name}<br>'
    for long_name, color in store_colors.items()
])

legend_html = """
{% macro html(this, kwargs) %}
<div style="
    position: fixed;
    bottom: 50px;
    left: 50px;
    width: 300px;
    background-color: white;
    border:2px solid grey;
    z-index:9999;
    font-size:14px;
    padding: 10px;
    border-radius: 5px;
">
    <b>Store Type Legend</b><br>
    """ + legend_items + """
</div>
{% endmacro %}
"""

legend = MacroElement()
legend._template = Template(legend_html)
map.add_child(legend)


folium.LayerControl().add_to(map)

In [74]:
map.save('assets/India_map.html')

## China

### Calculating SA%

In [75]:
china_df = df[df['Country'] == 'China']
china_df['Store Type'] = china_df['Store Type'].map(store_type)
china_pop = pd.read_excel('data/population_data.xlsx', sheet_name='China', usecols='A:C')

china_store_count = china_df.groupby(['Country', 'Province', 'Store Type']).size().reset_index(name='Count').pivot_table(
    index=['Country', 'Province'], 
    columns='Store Type', 
    values='Count', 
    fill_value=0
).reset_index()

china_rough = china_store_count.merge(
    multiplier_df,
    on='Country',
    how='left',
    suffixes=('', '_multiplier')
)

china_store_types = [col for col in china_store_count.columns if col not in ['Country', 'Province']]

china_store_count['SA'] = 0
for store in china_store_types:
    if store in multiplier_df.columns:
        china_store_count['SA'] += china_store_count[store] * china_rough[store + '_multiplier']


china_store_count = china_store_count.merge(
    china_pop,
    on=['Country', 'Province'],
    how='left'
)   
china_store_count['SA %'] = china_store_count['SA'] / china_store_count['Population'] * 100

china_store_count['Country'] = china_store_count['Country'].map(country_codes)
china_store_count

C:\Users\Ethan.loh\AppData\Local\Temp\ipykernel_15012\2495166663.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  china_df['Store Type'] = china_df['Store Type'].map(store_type)


Country        Province      EP     RAP          SA    Population  \
0      CHN           Anhui   650.0   897.0  26689000.0  6.144025e+07   
1      CHN       Chongqing    16.0    34.0    800000.0  3.227113e+07   
2      CHN          Fujian   142.0     3.0   3515000.0  4.182126e+07   
3      CHN           Gansu    12.0     1.0    306000.0  2.518919e+07   
4      CHN       Guangdong    95.0     1.0   2339500.0  1.268655e+08   
5      CHN         Guangxi    16.0     0.0    392000.0  5.046610e+07   
6      CHN         Guizhou    35.0     0.0    857500.0  3.882317e+07   
7      CHN           Hebei   447.0    60.0  11671500.0  7.511526e+07   
8      CHN    Heilongjiang     5.0     0.0    122500.0  3.206568e+07   
9      CHN           Henan  1003.0  1661.0  44505500.0  1.000381e+08   
10     CHN           Hubei   392.0     2.0   9628000.0  5.814347e+07   
11     CHN           Hunan   191.0     1.0   4691500.0  6.689462e+07   
12     CHN  Inner Mongolia     8.0     0.0    196000.0  2.421194e+07   
13     CHN         Jiangsu   683.0    12.0  16877500.0  8.532166e+07   
14     CHN         Jiangxi   251.0     0.0   6149500.0  4.549451e+07   
15     CHN           Jilin     2.0     0.0     49000.0  2.423640e+07   
16     CHN        Liaoning    37.0   208.0   3402500.0  4.287970e+07   
17     CHN         Ningxia    15.0     0.0    367500.0  7.251408e+06   
18     CHN         Qinghai     1.0     0.0     24500.0  5.964055e+06   
19     CHN         Shaanxi     7.0     0.0    171500.0  3.979656e+07   
20     CHN        Shandong  1399.0     5.0  34335500.0  1.022147e+08   
21     CHN          Shanxi    45.0    92.0   2206500.0  3.515195e+07   
22     CHN         Sichuan    53.0     0.0   1298500.0  8.424125e+07   
23     CHN         Tianjin    96.0     0.0   2352000.0  1.395987e+07   
24     CHN        Xinjiang    60.0     0.0   1470000.0  2.602734e+07   
25     CHN          Yunnan     7.0    61.0    903500.0  4.752883e+07   
26     CHN        Zhejiang   374.0     1.0   9175000.0  6.500464e+07   

         SA %  
0   43.438948  
1    2.478996  
2    8.404815  
3    1.214807  
4    1.844079  
5    0.776759  
6    2.208733  
7   15.538121  
8    0.382028  
9   44.488547  
10  16.559038  
11   7.013270  
12   0.809518  
13  19.781026  
14  13.517016  
15   0.202175  
16   7.934990  
17   5.067982  
18   0.410794  
19   0.430942  
20  33.591556  
21   6.277034  
22   1.541406  
23  16.848300  
24   5.647908  
25   1.900952  
26  14.114378

### Geojson Prep

In [76]:
geojson_data, geojson_df = get_geojsons(['CHN'])

china_province_dict = {
    'Anhui Province': 'Anhui',
    'Beijing Municipality': 'Beijing',
    'Chongqing Municipality': 'Chongqing',
    'Fujian Province': 'Fujian',
    'Gansu Province': 'Gansu',
    'Guangzhou Province': 'Guangdong', # weird
    'Guangxi Zhuang Autonomous Region': 'Guangxi',
    'Guizhou Province': 'Guizhou',
    'Hainan Province': 'Hainan',
    'Hebei Province': 'Hebei',
    'Heilongjiang Province': 'Heilongjiang',
    'Henan Province': 'Henan',
    'Hubei Province': 'Hubei',
    'Hunan Province': 'Hunan',
    'Inner Mongolia Autonomous Region': 'Inner Mongolia',
    'Jiangsu Province': 'Jiangsu',
    'Jiangxi Province': 'Jiangxi',
    'Jilin Province': 'Jilin',
    'Liaoning Province': 'Liaoning',
    'Ningxia Ningxia Hui Autonomous Region': 'Ningxia',
    'Qinghai Province': 'Qinghai',
    'Shaanxi Province': 'Shaanxi',
    'Shandong Province': 'Shandong',
    'Shanghai Municipality': 'Shanghai',
    'Shanxi Province': 'Shanxi',
    'Sichuan Province': 'Sichuan',
    'Tianjin Municipality': 'Tianjin',
    'Tibet Autonomous Region': 'Xizang',
    'Xinjiang Uyghur Autonomous Region': 'Xinjiang',
    'Yunnan Province': 'Yunnan',
    'Zhejiang Province': 'Zhejiang',
}   

geojson_df['shapeName'] = geojson_df['shapeName'].apply(
    lambda x: china_province_dict[x] if x in china_province_dict else x
)

geojson_df = geojson_df.merge(
    china_store_count[['Country', 'Province', 'SA %']],
    left_on=['shapeName', 'shapeGroup'],
    right_on=['Province', 'Country'],
    how='left'
)

geojson_df['SA %'] = geojson_df['SA %'].fillna(0)

geojson_df['SA %'] = geojson_df['SA %'].map(lambda x: f"{x:.5g}")
geojson_data = geojson_df.to_json()
geojson_data

present_store_types = china_df['Store Type'].unique()

geojson_df

Free Churro


shapeName shapeISO                  shapeID  \
0                                    Hainan      CHN  43563684B67556328368055   
1                           Taiwan Province      CHN  43563684B32372453033755   
2                                   Guangxi      CHN  43563684B59914390554750   
3                                    Fujian      CHN  43563684B30737817496648   
4                                    Yunnan      CHN  43563684B84540832148656   
5                                   Guizhou      CHN  43563684B78583622565599   
6                                   Jiangxi      CHN  43563684B87813050901813   
7                                     Hunan      CHN  43563684B64987462919315   
8                                  Zhejiang      CHN  43563684B73528730180553   
9                                  Shanghai      CHN  43563684B32591653033375   
10                                Chongqing      CHN  43563684B97743196909507   
11                                    Hubei      CHN  43563684B41908353419915   
12                                  Sichuan      CHN  43563684B14397599951889   
13                                    Anhui      CHN  43563684B75549295130005   
14                                  Jiangsu      CHN  43563684B64367354813847   
15                                    Henan      CHN  43563684B96917371447908   
16                                   Xizang      CHN  43563684B19802372559419   
17                                 Shandong      CHN  43563684B58995436924100   
18                                  Qinghai      CHN  43563684B46172434476792   
19                                  Ningxia      CHN  43563684B64666899633249   
20                                  Shaanxi      CHN  43563684B62959128536432   
21                                  Tianjin      CHN  43563684B84701301190484   
22                                   Shanxi      CHN  43563684B34303967365755   
23                                  Beijing      CHN  43563684B17418114845297   
24                                    Gansu      CHN  43563684B11053367304830   
25                                    Hebei      CHN  43563684B58229551045164   
26                                 Liaoning      CHN  43563684B26929678147954   
27                                    Jilin      CHN   43563684B3982601277390   
28                                 Xinjiang      CHN  43563684B50492231896073   
29                           Inner Mongolia      CHN  43563684B95381459098578   
30                             Heilongjiang      CHN  43563684B55920014778896   
31      Macau Special Administrative Region      CHN  43563684B97104103456250   
32  Hong Kong Special Administrative Region      CHN  43563684B69230098435171   
33                                Guangdong      CHN  43563684B38891657012300   

   shapeGroup shapeType                                           geometry  \
0         CHN      ADM1  POLYGON ((110.92512 20.00042, 110.92165 20.159...   
1         CHN      ADM1  POLYGON ((121.73295 25.16218, 121.61853 25.281...   
2         CHN      ADM1  POLYGON ((112.00096 24.85742, 111.96945 24.861...   
3         CHN      ADM1  MULTIPOLYGON (((118.48218 24.45517, 118.44099 ...   
4         CHN      ADM1  POLYGON ((104.58105 24.81737, 104.58275 24.859...   
5         CHN      ADM1  POLYGON ((109.53818 26.12561, 109.53908 26.128...   
6         CHN      ADM1  POLYGON ((118.59095 28.39009, 118.59998 28.398...   
7         CHN      ADM1  POLYGON ((112.00096 24.85742, 112.00255 24.857...   
8         CHN      ADM1  POLYGON ((120.5414 27.28741, 120.6442 27.36964...   
9         CHN      ADM1  MULTIPOLYGON (((122.04414 31.31785, 121.85809 ...   
10        CHN      ADM1  POLYGON ((109.33745 28.61259, 109.34672 29.236...   
11        CHN      ADM1  POLYGON ((116.2457 29.88968, 116.22494 30.0586...   
12        CHN      ADM1  POLYGON ((105.36946 27.86563, 105.41091 27.871...   
13        CHN      ADM1  POLYGON ((118.29055 29.5127, 118.31396 29.4872...   
14        CHN      ADM1  POL

### Map Making

In [77]:
sa_dict = china_store_count.groupby("Province")["SA %"].max().to_dict()

map = folium.Map(
    location=[35.8617, 104.1954], 
    zoom_start=4
)

folium.TileLayer(
    tiles='https://mt1.google.com/vt/lyrs=m&x={x}&y={y}&z={z}',
    attr='Google',
    name='Google Maps'  
).add_to(map)

folium.GeoJson(
    geojson_data,
    style_function=lambda feature: {
        "fillColor": linear(min(sa_dict.get(feature["properties"]["shapeName"], 0), 100)),
        "color": "black",
        "weight": 1,
        "fillOpacity": 0.6,
    },
    tooltip=folium.GeoJsonTooltip(
        fields=["shapeName", 'SA %'],
        aliases=["Region:", 'SA %'],
    ),
    control=False,
).add_to(map)

linear.caption = "SA % (0–100 scale)"
linear.add_to(map)

for store in present_store_types:
    make_points(china_df, store, map)

# make_points_clustered(china_df, 'FRE (MMO, EMO, EM, ER)', map)

store_colors = {
    store_type: get_store_type_color(store_type)
    for store_type in present_store_types
}

legend_items = ''.join([
    f'<i style="background:{color}; width:10px; height:10px; display:inline-block; margin-right:5px;"></i>{long_name}<br>'
    for long_name, color in store_colors.items()
])

legend_html = """
{% macro html(this, kwargs) %}
<div style="
    position: fixed;
    bottom: 50px;
    left: 50px;
    width: 300px;
    background-color: white;
    border:2px solid grey;
    z-index:9999;
    font-size:14px;
    padding: 10px;
    border-radius: 5px;
">
    <b>Store Type Legend</b><br>
    """ + legend_items + """
</div>
{% endmacro %}
"""

legend = MacroElement()
legend._template = Template(legend_html)
map.add_child(legend)


folium.LayerControl().add_to(map)


In [78]:
map.save('assets/China_map.html')

## Africa

### Calculating SA%
code is slightly differnt because Africa does VAH/VC catchment size differently

In [79]:
africa_df = df[(df['Country'] == 'Kenya') | 
                    (df['Country'] == 'Liberia') | 
                    (df['Country'] == 'Rwanda') | 
                    (df['Country'] == 'South Africa') | 
                    (df['Country'] == 'Gambia') | 
                    (df['Country'] == 'Zambia') | 
                    (df['Country'] == 'Malawi') |
                    (df['Country'] == 'Ghana') |
                    (df['Country'] == 'Eswatini')]


# africa_df = africa_df.merge(
#     # whatever file Chiara decides to send when she decides to send
#     how='left',
# )

reverse_map = {v: k for k, v in store_type.items()}
def fill_population_access(row):
    if pd.isna(row['Population Access']):
        country = row['Country']
        store_type = row['Store Type']
        # import pdb; pdb.set_trace()
        try:
            return multiplier_df.loc[country, store_type]
        except KeyError:
            return row['Population Access']  # fallback
    return row['Population Access']

# Till Chiara sends it:
africa_df['Population Access'] = np.nan

africa_df['Store Type'] = africa_df['Store Type'].map(store_type)
africa_df['Population Access'] = africa_df.apply(fill_population_access, axis=1)
africa_df = africa_df.dropna(subset=['Latitude', 'Longitude'])

C:\Users\Ethan.loh\AppData\Local\Temp\ipykernel_15012\3684399840.py:30: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  africa_df['Population Access'] = np.nan
C:\Users\Ethan.loh\AppData\Local\Temp\ipykernel_15012\3684399840.py:32: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  africa_df['Store Type'] = africa_df['Store Type'].map(store_type)
C:\Users\Ethan.loh\AppData\Local\Temp\ipykernel_15012\3684399840.py:33: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try us

In [80]:
africa_vah_vc = africa_df[africa_df['Store Type'].isin(['VAH', 'VC'])]
africa_df = africa_df[(africa_df['Store Type'] != 'VAH') | (africa_df['Store Type'] != 'VC')]

africa_pop = pd.read_excel('data/population_data.xlsx', sheet_name='Africa', usecols='A:C')

africa_store_count = africa_df.groupby(['Country', 'Province', 'Store Type']).size().reset_index(name='Count').pivot_table(
    index=['Country', 'Province'], 
    columns='Store Type', 
    values='Count', 
    fill_value=0
).reset_index()

africa_rough = africa_store_count.merge(
    multiplier_df,
    on='Country',
    how='left',
    suffixes=('', '_multiplier')
)

africa_store_types = [col for col in africa_store_count.columns if col not in ['Country', 'Province']]

africa_store_count['SA'] = 0
for store in africa_store_types:
    if (store in multiplier_df.columns) & (store != 'VAH') & (store != 'VC'):
        africa_store_count['SA'] += africa_store_count[store] * africa_rough[store + '_multiplier']


africa_store_count = africa_store_count.merge(
    africa_pop,
    on=['Country', 'Province'],
    how='left'
)   

vah_vc_sum = africa_vah_vc.groupby("Province")["Population Access"].sum()
africa_store_count["SA"] += africa_store_count["Province"].map(vah_vc_sum).fillna(0)


africa_store_count['SA %'] = africa_store_count['SA'] / africa_store_count['Population'] * 100

africa_store_count['Country'] = africa_store_count['Country'].map(country_codes)

africa_store_count

Country           Province   EP  FRE (MMO, EMO, EM, ER)  VAH    VC  \
0      SWZ            Manzini  0.0                     0.0  0.0   1.0   
1      GMB              Basse  0.0                     0.0  0.0   1.0   
2      GMB            Brikama  0.0                     0.0  0.0   2.0   
3      GMB        Janjanbureh  0.0                     0.0  0.0   1.0   
4      GMB           Kanifeng  0.0                     0.0  0.0   1.0   
5      GMB            Kerewan  0.0                     0.0  0.0   1.0   
6      GMB         Mansakonko  0.0                     0.0  0.0   1.0   
7      GHA     Central Region  0.0                     0.0  0.0   1.0   
8      KEN            Baringo  0.0                     6.0  0.0   0.0   
9      KEN            Bungoma  0.0                    34.0  0.0   1.0   
10     KEN              Busia  0.0                    14.0  0.0   1.0   
11     KEN    Elgeyo-Marakwet  0.0                     5.0  0.0   0.0   
12     KEN               Embu  0.0                     0.0  0.0   1.0   
13     KEN            Garissa  0.0                     0.0  0.0   1.0   
14     KEN           Homa Bay  0.0                    29.0  0.0   0.0   
15     KEN            Kajiado  0.0                     0.0  0.0   2.0   
16     KEN           Kakamega  0.0                     0.0  0.0   2.0   
17     KEN            Kericho  0.0                     5.0  0.0   0.0   
18     KEN             Kiambu  0.0                     0.0  1.0   1.0   
19     KEN              Kisii  0.0                     0.0  0.0   2.0   
20     KEN             Kisumu  0.0                     2.0  0.0   0.0   
21     KEN              Kwale  0.0                     0.0  0.0   2.0   
22     KEN           Machakos  0.0                     0.0  0.0   1.0   
23     KEN            Makueni  0.0                     0.0  1.0   1.0   
24     KEN               Meru  0.0                     0.0  1.0   0.0   
25     KEN             Migori  0.0                     6.0  0.0   0.0   
26     KEN           Murang'a  0.0                     0.0  0.0   1.0   
27     KEN            Nairobi  0.0                     0.0  0.0   1.0   
28     KEN              Nandi  0.0                    26.0  0.0   0.0   
29     KEN              Narok  1.0                     0.0  0.0   1.0   
30     KEN            Nyamira  0.0                    16.0  0.0   4.0   
31     KEN              Siaya  0.0                    17.0  0.0   0.0   
32     KEN        Trans Nzoia  0.0                     2.0  0.0   0.0   
33     KEN        Uasin Gishu  0.0                    39.0  0.0   2.0   
34     KEN             Vihiga  0.0                     0.0  1.0   0.0   
35     LBR               Bomi  0.0                     0.0  0.0   1.0   
36     LBR               Bong  0.0                     0.0  0.0   1.0   
37     LBR           Maryland  0.0                     0.0  0.0   1.0   
38     LBR        Montserrado  0.0                     0.0  2.0   3.0   
39     LBR              Nimba  0.0                     0.0  0.0   1.0   
40     MWI     Central Region  0.0                     0.0  0.0   4.0   
41     MWI    Southern Region  0.0                     0.0  0.0   6.0   
42     RWA     City of Kigali  0.0                     0.0  0.0   6.0   
43     RWA   Eastern Province  0.0                     0.0  0.0   8.0   
44     RWA  Northern Province  0.0                     0.0  0.0   7.0   
45     RWA  Southern Province  0.0                     0.0  0.0  12.0   
46     RWA   Western Province  0.0                     0.0  0.0  10.0   
47     ZAF            Gauteng  0.0                     0.0  0.0   3.0   
48     ZAF       Nothern Cape  0.0                     0.0  0.0   2.0   
49     ZMB            Central  1.0                     0.0  1.0   5.0   
50     ZMB         Copperbelt  0.0                     0.0  0.0   6.0   
51     ZMB            Eastern  0.0                     0.0  0.0   8.0   
52     ZMB            Luapula  0.0                     0.0  1.0   6.0   
53     ZMB             Lusaka  1.0                     0.0  1

### Geojson Prep

if you need a dict just make it and map it. 

In [81]:
africa_codes = ['KEN', 'LBR', 'RWA', 'ZAF', 'GMB', 'ZMB', 'MWI', 'GHA', 'SWZ']
geojson_data, geojson_df = get_geojsons(africa_codes)

geojson_df = geojson_df.merge(
    africa_store_count[['Country', 'Province', 'SA %']],
    left_on=['shapeName', 'shapeGroup'],
    right_on=['Province', 'Country'],
    how='left'
)

geojson_df['SA %'] = geojson_df['SA %'].fillna(0)

geojson_df['SA %'] = geojson_df['SA %'].map(lambda x: f"{x:.5g}")
geojson_data = geojson_df.to_json()
geojson_data

present_store_types = africa_df['Store Type'].unique()

geojson_df

Free Churro


shapeName shapeISO                  shapeID shapeGroup  \
0                 Turkana    KE-43  32016919B72266624462344        KEN   
1                Marsabit    KE-25  32016919B63496705134089        KEN   
2                 Mandera    KE-24   32016919B2031803566233        KEN   
3                   Wajir    KE-46  32016919B89873713911655        KEN   
4              West Pokot    KE-47  32016919B96045830258165        KEN   
..                    ...      ...                      ...        ...   
112  Greater Accra Region    GH-AA  69750345B46963341226980        GHA   
113               Manzini    SZ-MA   75366066B3567364273406        SWZ   
114               Lubombo    SZ-LU  75366066B12234306804593        SWZ   
115            Shiselweni    SZ-SH  75366066B21527038718027        SWZ   
116                Hhohho    SZ-HH  75366066B25905390127614        SWZ   

    shapeType                                           geometry Country  \
0        ADM1  POLYGON ((36.05061 4.45622, 35.94395 4.54803, ...     NaN   
1        ADM1  POLYGON ((36.60089 2.40574, 36.60454 2.4017, 3...     NaN   
2        ADM1  POLYGON ((40.99195 2.17919, 40.9926 2.52318, 4...     NaN   
3        ADM1  POLYGON ((38.96255 2.09739, 38.97986 2.07774, ...     NaN   
4        ADM1  POLYGON ((34.94278 2.45547, 34.93109 2.45501, ...     NaN   
..        ...                                                ...     ...   
112      ADM1  POLYGON ((-0.49885 5.72491, -0.49944 5.71532, ...     NaN   
113      ADM1  POLYGON ((30.89835 -26.31553, 30.89186 -26.320...     SWZ   
114      ADM1  POLYGON ((31.48113 -26.77139, 31.48871 -26.779...     NaN   
115      ADM1  POLYGON ((30.89043 -26.78709, 30.89191 -26.785...     NaN   
116      ADM1  POLYGON ((31.67791 -26.16314, 31.67601 -26.151...     NaN   

    Province    SA %  
0        NaN       0  
1        NaN       0  
2        NaN       0  
3        NaN       0  
4        NaN       0  
..       ...     ...  
112      NaN       0  
113  Manzini  79.786  
114      NaN       0  
115      NaN       0  
116      NaN       0  

[117 rows x 9 columns]

### Map Making

In [82]:
sa_dict = africa_store_count.groupby("Province")["SA %"].max().to_dict()

map = folium.Map(
    location=[1.5, 17.0], 
    zoom_start=4
)

folium.TileLayer(
    tiles='https://mt1.google.com/vt/lyrs=m&x={x}&y={y}&z={z}',
    attr='Google',
    name='Google Maps'  
).add_to(map)

folium.GeoJson(
    geojson_data,
    style_function=lambda feature: {
        "fillColor": linear(min(sa_dict.get(feature["properties"]["shapeName"], 0), 100)),
        "color": "black",
        "weight": 1,
        "fillOpacity": 0.6,
    },
    tooltip=folium.GeoJsonTooltip(
        fields=["shapeName", 'SA %'],
        aliases=["Region:", 'SA %'],
    ),
    control=False,
).add_to(map)

linear.caption = "SA % (0–100 scale)"
linear.add_to(map)

for store in present_store_types:
    make_points(africa_df, store, map)

store_colors = {
    store_type: get_store_type_color(store_type)
    for store_type in present_store_types
}

legend_items = ''.join([
    f'<i style="background:{color}; width:10px; height:10px; display:inline-block; margin-right:5px;"></i>{long_name}<br>'
    for long_name, color in store_colors.items()
])

legend_html = """
{% macro html(this, kwargs) %}
<div style="
    position: fixed;
    bottom: 50px;
    left: 50px;
    width: 300px;
    background-color: white;
    border:2px solid grey;
    z-index:9999;
    font-size:14px;
    padding: 10px;
    border-radius: 5px;
">
    <b>Store Type Legend</b><br>
    """ + legend_items + """
</div>
{% endmacro %}
"""

legend = MacroElement()
legend._template = Template(legend_html)
map.add_child(legend)


folium.LayerControl().add_to(map)

In [83]:
map.save('assets/Africa_map.html')